In [108]:
import pandas as pd

In [109]:
import plotly.graph_objects as go

In [110]:
import plotly.express as px

In [111]:
def fix_time(x):
    if not '+' in x:
        return 0
    else:  
        s = x.split(' ')
        if 'min' in x:
            return 60*int(s[1]) + int(s[-2])
        else:
            return int(s[-2])

In [112]:
df_giro = pd.read_csv('./data/giro.csv', sep=';', names=['position','name','team','time'])

In [113]:
df_giro['position'] = df_giro['position'].apply(lambda x:int(x.split('.')[0]))

In [114]:
df_giro['country'] = df_giro['name'].apply(lambda x:x.split(' ')[0])

In [115]:
df_giro['name'] = df_giro['name'].apply(lambda x:' '.join(x.split(' ')[1:]))

In [116]:
df_giro.loc[(df_giro['time']!=df_giro['time'])]

Empty DataFrame
Columns: [position, name, team, time, country]
Index: []

In [117]:
df_giro['time'] = df_giro['time'].apply(fix_time)

In [118]:
dict_flags = {
    'ITA':'🇮🇹',
    'NOR':'🇳🇴',
    'POR':'🇵🇹',
    'FRA':'🇫🇷',
    'NED':'🇳🇱',
    'BEL':'🇧🇪',
    'GER':'🇩🇪',
    'AUT':'🇦🇹',
    'RUS':'🇷🇺',
    'ESP':'🇪🇸',
    'USA':'🇺🇸',
    'HUN':'🇭🇺',
    'GBR':'🇬🇧',
    'COL':'🇨🇴',
    'IRL':'🇮🇪'
}

In [119]:
df_giro['country'].unique()

array(['ITA', 'NOR', 'POR', 'FRA', 'NED', 'BEL', 'GER', 'AUT', 'RUS',
       'ESP', 'USA', 'HUN', 'GBR', 'COL', 'IRL'], dtype=object)

In [120]:
df_giro['country'] = df_giro['country'].apply(lambda x:dict_flags[x])

In [121]:
df_giro['name'] = df_giro['country'] + ' ' + df_giro['name']

In [122]:
top_5_names = df_giro.tail(10).head(5)

In [123]:
format_time = lambda x:f'{x//60} min {x%60} seg'

In [124]:
for name in top_5_names.to_dict(orient='records'):
    print(f'{name["position"]}. {name["name"]} - {name["team"]}: +{format_time(name["time"])}')

1. 🇨🇴 Egan Bernal - Ineos Grenadiers: +0 min 0 seg
2. 🇮🇹 Damiano Caruso - Bahrain Victorious: +2 min 29 seg
3. 🇬🇧 Simon Yates - Team BikeExchange: +2 min 49 seg
4. 🇷🇺 Aleksandr Vlasov - Astana-Premier Tech: +6 min 11 seg
5. 🇬🇧 Hugh Carthy - EF Education-Nippo: +7 min 10 seg


In [125]:
top_5_names['name_position'] = top_5_names['position'].astype(str) + '. ' + top_5_names['name']

In [126]:
top_5_names.index = top_5_names['name']

In [127]:
top_5_names = top_5_names['name_position'].to_dict()

In [128]:
df_giro['name'] = df_giro['name'].apply(lambda x: top_5_names[x] if x in top_5_names else x)

In [129]:
stage = []
for n in range(len(df_giro)//10):
    stage = stage + [n+1]*10

In [130]:
df_giro['stage'] = stage

In [131]:
last_stage = df_giro['stage'].max()

In [132]:
df_giro = df_giro.loc[df_giro['stage']>=0]

In [133]:
names = df_giro.loc[
    (
        (df_giro['stage']==df_giro['stage'].max()) &
        (df_giro['position']<=5)
    ) #|
    #(
    #    (df_giro['position']==1)
    #)
]['name'].unique()

In [134]:
# df_giro = df_giro.loc[df_giro['name'].isin(names)]

In [135]:
df_giro = df_giro[
    [
        'name',
        'time',
        'stage'
    ]
]

In [136]:
time_max = df_giro['time'].max()

In [137]:
#time_max = (1+time_max//100)*100

In [138]:
time_max

835

In [139]:
df_giro = df_giro.pivot(
    columns=['name'],
    index='stage'
)['time']

In [140]:
df_giro = df_giro.fillna(time_max+30)

In [141]:
df_index = (pd.Series(list(range(1,max(df_giro.index)*100+1,1)), name='stage')/100).to_frame()

In [142]:
df_index = df_index.loc[df_index['stage']>=0]

In [143]:
df_giro = df_giro.reset_index()

In [144]:
df_giro['stage'] = df_giro['stage'].astype(float)

In [145]:
df_giro = pd.merge(df_index, df_giro, on='stage', how='left')

In [146]:
df_giro = df_giro.fillna(method='bfill')

In [147]:
df_giro = df_giro.rolling(100, win_type='triang').mean()

In [148]:
df_giro

stage  1. 🇨🇴 Egan Bernal  2. 🇮🇹 Damiano Caruso  3. 🇬🇧 Simon Yates  \
0        NaN                NaN                   NaN                NaN   
1        NaN                NaN                   NaN                NaN   
2        NaN                NaN                   NaN                NaN   
3        NaN                NaN                   NaN                NaN   
4        NaN                NaN                   NaN                NaN   
...      ...                ...                   ...                ...   
1895  18.465                0.0              148.9744           169.1088   
1896  18.475                0.0              148.9856           169.0612   
1897  18.485                0.0              148.9936           169.0272   
1898  18.495                0.0              148.9984           169.0068   
1899  18.505                0.0              149.0000           169.0000   

      4. 🇷🇺 Aleksandr Vlasov  5. 🇬🇧 Hugh Carthy  🇦🇹 Matthias Brändle  \
0                        NaN                NaN                  NaN   
1                        NaN                NaN                  NaN   
2                        NaN                NaN                  NaN   
3                        NaN                NaN                  NaN   
4                        NaN                NaN                  NaN   
...                      ...                ...                  ...   
1895                370.9744           429.8048                865.0   
1896                370.9856           429.8902                865.0   
1897                370.9936           429.9512                865.0   
1898                370.9984           429.9878                865.0   
1899                371.0000           430.0000                865.0   

      🇧🇪 Louis Vervaeke  🇧🇪 Remco Evenepoel  🇨🇴 Daniel Felipe Martínez  ...  \
0                   NaN                 NaN                        NaN  ...   
1                   NaN                 NaN                        NaN  ...   
2                   NaN                 NaN                        NaN  ...   
3                   NaN                 NaN                        NaN  ...   
4                   NaN                 NaN                        NaN  ...   
...                 ...                 ...                        ...  ...   
1895              865.0               865.0                    461.920  ...   
1896              865.0               865.0                    461.955  ...   
1897              865.0               865.0                    461.980  ...   
1898              865.0               865.0                    461.995  ...   
1899              865.0               865.0                    462.000  ...   

      🇮🇹 Diego Ulissi  🇮🇹 Edoardo Affini  🇮🇹 Filippo Ganna  🇮🇹 Gianni Moscon  \
0                 NaN                NaN               NaN               NaN   
1                 NaN                NaN               NaN               NaN   
2                 NaN                NaN               NaN               NaN   
3                 NaN                NaN               NaN               NaN   
4                 NaN                NaN               NaN               NaN   
...               ...                ...               ...               ...   
1895            865.0              865.0             865.0             865.0   
1896            865.0              865.0             865.0             865.0   
1897            865.0              865.0             865.0             865.0   
1898            865.0              865.0             865.0             865.0   
1899            865.0              865.0             865.0             865.0   

      🇮🇹 Giulio Ciccone  🇳🇱 Jos van Emden  🇳🇴 Tobias Foss  🇵🇹 João Almeida  \
0                   NaN               NaN             NaN              NaN   
1                   NaN               NaN             NaN              NaN   
2                   NaN               NaN             NaN              NaN   
3      

In [149]:
fig = go.Figure()

top_5_color_list = [
    #'#4E79A7',
    '#A0CBE8',
    #'#F28E2B',
    '#9C755F',
    '#59A14F',
    '#EDC948'
]

for name in df_giro.columns:
    if name != 'stage':
        line_dict = {
            'width':0.6
        }
        is_leader = list(df_giro.loc[df_giro['stage']==df_giro['stage'].max()][name])[0]==0
        if (name in names) and not is_leader:
            line_dict['color']=top_5_color_list.pop()
            line_dict['width']=4
        if is_leader:
            line_dict['color']='#FF8BC1'
            line_dict['width']=9
        fig.add_trace(
            go.Scatter(
                #x=list(df_giro['stage']) + [int(list(df_giro['stage'])[-1]+1)],
                #y=list(df_giro[name]) + [list(df_giro[name])[-1]],
                x=df_giro['stage']+0.7,
                y=df_giro[name],
                name=name,
                line=line_dict
            )
        )

fig.update_layout(
    yaxis = dict(title='Diferencia con el líder (segundos)'),
    yaxis_range=[time_max+10, -5]
    #yaxis_range=[370, -5]
)
fig.update_layout(
    xaxis = dict(
        title = 'Etapa',
        tickmode = 'linear',
        tick0 = 1,
        dtick = 1
    ),
    yaxis = dict(
        tickmode = 'linear',
        dtick = 60
    )
)
fig.update_layout(
    title = '🚴 Giro de Italia 🎀 Top 10 por etapa',
    title_x=0.25
)

fig.update_layout(legend_title_text=f'Top 5 en etapa {last_stage}')

for trace in fig['data']: 
    if (not trace['name'] in names):
        trace['showlegend'] = False
        
fig.layout.plot_bgcolor = '#eee'
fig.layout.paper_bgcolor = '#fff'

fig.show()

In [150]:
fig.write_html('../docs/giro.html')